**Note**: Click [here](https://nbviewer.jupyter.org/gist/WetHat/6a8e38fb92ab831d8cdb5d66f2d2e524/PY-EquationRegistry.ipynb)
to view the full fidelity version of this notebook with
[nbviewer](https://nbviewer.jupyter.org/).

# A Simple Registry for Managing and Auto-numbering _SymPy_ Equations



The combination of [sympy](https://www.sympy.org) and [Jupyter Notebooks](https://jupyter.org/) is
an efficient way to post experiments or articles involving [computer algebra](https://en.wikipedia.org/wiki/Computer_algebra). However, as the notebook gets bigger following challenges may arise:
* Manual numbering of equations (so that they can be referred to in downstream equations or text) becomes labor intensive.
  Particularly if the order of notebook cells need to be changed.
* The Python namespace becomes cluttered with variables holding intermediary results.
  Local variables defined else where make the notebook harder to understand and also sometimes
  cause unforeseen side effects.

In this notebook we show a simple utility class to organize [sympy](https://www.sympy.org) expressions. 

# The Notebook Equation Registry Class

The _registry_ class implements a dictionary for `sympy` expressions. It is expected that this class
is mostly used for equations, so it is named `EquationRegistry`, though it can manage any type of `sympy`
expressions.

The implementation in this notebook offers following features:

* Github compatible rendering mode or Jupyter mode
* Easy registration process.
* Access to previously registered expressions by name
* Expression names can be used to create Markdown links to navigate to the
  notebook cells where the expression is displayed:
  
  ~~~ markdown
    Take me to equation registered under the name [foo](#foo)
  ~~~
* Auto numbering of registered expressions (GitHub rendering):
  $$
  \begin{matrix}\boxed{f(x) = b  x^2 + c} & (11) \end{matrix}
  $$
  
  or with optional display of the equation name (GitHub rendering):
  $$
  \begin{matrix}\boxed{f(x) = b  x^2 + c} & (11) \  \text{Energy}\end{matrix}
  $$
* Autocompletion of registered expressions in the notebook cell editor:
  
  ![Autocomplete](https://gist.github.com/WetHat/6a8e38fb92ab831d8cdb5d66f2d2e524/raw/ed180f06d6bfd29bd4557dbb1e66504c1e643273/Xautocomplete.png)
* Automatic renumbering of registered expressions if cell order has changed (Requires re-running of all notebook cells).

## class `EquationRegistry`

**`EquationRegistry(show_names = False, github = True)`**

Create a notebook registry to manage `sympy` expressions.

`sympy` expressions can be registered with the registry simply by assigning
it to an (non-)existing property like so:
~~~ python
ER.SomeName = Eq(a,b) # ER is a registry object
~~~
Once registered an equation can be retrieved from the registry by using
its property name.

~~~ python
ER.SomeName # ER is a registry object
~~~

> **Args**

> **`show_names: bool = False`**
> : Optional flag to configure the registry to display equation names
>   along with their sequence number.
>  
>   if `true` the equation name is added to the sequence number:
>   $$
>   \begin{matrix}\boxed{f(x) = b  x^2 + c} & (11) \  \text{Energy}\end{matrix}
>   $$
>  
> **`github: bool = True`**
> : Optional flag to configure LaTeX rendering mode. `True` to generate
>   a less aligned, GitHub compatible LaTex notation. `False` to generate
>   a  LaTex notation which is optimized for notebook rendering.
- - -

**Methods**

**`__setattr__(name: str, value)`**

> _Dunder_ method to allow the on-the-fly creation of new registration properties.
>
> **Args**
>
> **`name: str`**
> : The registration name of a `sympy` expression.
>
> **`value`**
> : A `sympy` expression. Most likely an equation object (`Eq`).

**`__call__(name: str)`**

> _Dunder_ method to render the `sympy` expression with the given name
> in an output cell by _calling_ the registry object.
>
> ~~~ python
> ER('foo') # display math for equation 'foo' in the output cell
> ~~~
>
> When the equation is displyed an HTML anchor (bookmark) is established
> so that Markdown links navigating to the output cell can be created like so:
>
> ~~~ markdown
> Take me to the equation I registered under the name [foo](#foo)
> ~~~
>
> **Args**
>
> **`name: str`**
> : The name of a registered `sympy` expression

In [1]:
import sympy as sp
from IPython.display import Math, Markdown

In [2]:
class EquationRegistry():

    def __init__(self, show_names: bool = False, github: bool = True):
        # bypass self.__setattr__
        self.__dict__['_indexmap'] = {}
        self.__dict__['_show_names'] = show_names
        self.__dict__['_github'] = github

    def __setattr__(self, name: str, value):
        index = self._indexmap.get(name, 0)
        if index == 0:  # a new field is requested
            self._indexmap[name] = len(self._indexmap) + 1
        self.__dict__[name] = value

    def __call__(self, name: str):
        index = self._indexmap[name]
        self._indexmap[name] = index  # mark as published
        display(Markdown(f'\n<a name="{name}"/>')) # create an HTML anchor
        if self._github:
            label = '(' + str(index) + ')' + ((r'\ \text{' + name + r'}') if self._show_names else '')
            math = Math(r'\begin{matrix}\boxed{\displaystyle ' \
                        + sp.latex(self.__dict__[name]) \
                        + r'} & ' \
                        + label\
                        + r'\end{matrix}')
        else:
            label = str(index) + ((' - ' + name) if self._show_names else '')
            math  = Math(r'\boxed{' \
                         + sp.latex(self.__dict__[name]) \
                         + r'} \tag{' \
                         + label \
                         + '}')
        display(math) # render the expression

# Showcase

In this section we demonstrate a typical use case for the equation registry.
To get started we get the required Python imports out of the way.

In [3]:
from sympy import Sum, Eq, IndexedBase, diff, Function, factor_terms, expand
from sympy.abc import *

Now we create an instance of the registry. We use one registry for the entire
notebook. However, it is conceivable that in some cases more than one registry may be created.

We configure the registry to also display equation names after the number. Since we want to publish this notebook as a GitHub Gist we choose `github = True`.

In [4]:
ER = EquationRegistry(show_names = True, github=True) # create the equation registry for this notebook

Next we create a simple function which could represent the error $\epsilon_i$
for a value $p_i$ from a data set containing $n$ values. The exact details are not important
here. We just need something to do some math with.

We register the corresponding `sympy` equation under the name `error` and also display it:

In [5]:
epsilon = IndexedBase('\epsilon')
p = IndexedBase('p')

ER.error = Eq(epsilon[i], x - p[i])  # define and register equation
ER('error')  # Display registered equation


<a name="error"/>

<IPython.core.display.Math object>

We get the previously defined `error` function from the registry with `ER.error`
and derive a so called energy function $E(x)$.
We register the corresponding `sympy` equation under the name `energy` and display it.
Note how `ER.error.lhs` and `ER.error.rhs` is used to access the left hand and right hand side of the registered
equation.

In [6]:
E = Function('E')

ER.energy = Eq(E(x), Sum(ER.error.rhs**2, (i, 0, n - 1)) / n)
ER('energy')


<a name="energy"/>

<IPython.core.display.Math object>

We now get the `energy` equation from the registry (`ER.energy`) to compute a derivative which we then register under the name `dE_dx`:

In [7]:
ER.dE_dx = Eq(diff(ER.energy.lhs, x), ER.energy.rhs.diff(x))
ER('dE_dx')


<a name="dE_dx"/>

<IPython.core.display.Math object>

Finally we perform some simplification:

In [8]:
ER.dE_dx_simple = Eq(ER.dE_dx.lhs, factor_terms(expand(ER.dE_dx.rhs)).doit())
ER('dE_dx_simple')


<a name="dE_dx_simple"/>

<IPython.core.display.Math object>

Finally take me back to the equation I registered under the name [error](#error). We can
also generate latex style links like so: [$E(x)$](#energy)

**Note** Hyperlinks do not work in GitHub Gist rendering to view this notebook in full fidelity use
[this link](https://nbviewer.jupyter.org/gist/WetHat/6a8e38fb92ab831d8cdb5d66f2d2e524/PY-EquationRegistry.ipynb) to open the notebook in the
[nbviewer](https://nbviewer.jupyter.org/) web service.

# Appendix

In [9]:
from jnbBuffs.manifest import notebook_manifest

## Packages Used In The Making Of This Notebook

In [10]:
notebook_manifest('jupyterlab', 'sympy', 'jnbBuffs')

| Component                         | Version                    | Description          |
| --------------------------------- | -------------------------- | -------------------- |
| [Python](https://www.python.org/) | 3.8.6   | Programming Language |
| [jnbBuffs](https://github.com/WetHat/jupyter-notebooks) | 0.1.8 | Utilities for authoring JupyterLab Python notebooks. |
| [jupyterlab](http://jupyter.org) | 3.0.12 | The JupyterLab server extension. |
| [sympy](https://sympy.org) | 1.7.1 | Computer algebra system (CAS) in Python |